# __Workshop 4__
## __Trading Algorithmique__

### Importation des librairies

```
pip install yfinance pandas numpy matplotlib ta plotly
```

In [1]:
# import des bibliothèques
import yfinance as yf
import pandas as pd
from datetime import datetime, timedelta
from ta.trend import IchimokuIndicator
import matplotlib.pyplot as plt
from datetime import datetime, timedelta
import numpy as np
import plotly.graph_objects as go
import plotly.express as px

## __Stratégie 1 : Ichimoku Cloud__

### __Calcul des indicateurs__

On note $P_t$ le prix de clôture à la date $t$. Formules pour les calculs des indicateurs :

$$
\begin{align*}
\text{(Tenkan Sen)}_t &= \frac{\text{High}_{t-9:t} + \text{Low}_{t-9:t}}{2} \\
\text{(Kijun Sen)}_t &= \frac{\text{High}_{t-26:t} + \text{Low}_{t-26:t}}{2} \\
\text{(Ichimoku A)}_t &= \frac{\text{(Tenkan Sen)}_t + \text{(Kijun Sen)}_t}{2} \\ 
\text{(Ichimoku B)}_t &= \frac{\text{High}_{t-52:t} + \text{Low}_{t-52:t}}{2} \\
\text{(Ichimoku Max)}_t &= \max(\text{Ichimoku A}_{t}, \text{Ichimoku B}_{t}) \\
\text{(Ichimoku Min)}_t &= \min(\text{Ichimoku A}_{t}, \text{Ichimoku B}_{t})
\end{align*}
$$

In [2]:
# Spécifiez le symbole boursier EUR/USD
symbol = "DOT-EUR" # Ne pas changer le symbole

# Date de fin
end_date = datetime.now()

# Durée de l'étude (T jours)
T = 50
start_date = end_date - timedelta(days=T)

# Récupérez les données
data = yf.download(symbol, start=start_date, end=end_date, interval="5m")
data.index = data.index.tz_convert(None)

# Créez l'indicateur Ichimoku
ichimoku = IchimokuIndicator(high=data["High"], low=data["Low"])

# Ajoutez les colonnes correspondant au nuage Ichimoku à votre DataFrame
data["Ichimoku_A"] = ichimoku.ichimoku_a()
data["Ichimoku_B"] = ichimoku.ichimoku_b()

# Sur le min et le max les conditions logique de sortit du nuage seront plus simple a exprimer
data["Ichimoku_Min"] = data[["Ichimoku_A", "Ichimoku_B"]].min(axis=1)
data["Ichimoku_Max"] = data[["Ichimoku_A", "Ichimoku_B"]].max(axis=1)

[*********************100%%**********************]  1 of 1 completed


### __Affichage des indicateurs__

In [21]:
# Plot avec Plotly
# ------------------------------------
fig = go.Figure(
    data=[
        go.Candlestick(
            x=data.index,
            open=data["Open"],
            high=data["High"],
            low=data["Low"],
            close=data["Close"],
        )
    ]
)

fig.add_trace(
    go.Scatter(
        x=data.index,
        y=data["Ichimoku_A"],
        line=dict(color="blue", width=1),
        name="Ichimoku A",
    )
)
fig.add_trace(
    go.Scatter(
        x=data.index,
        y=data["Ichimoku_B"],
        line=dict(color="red", width=1),
        name="Ichimoku B",
    )
)
fig.add_trace(
    go.Scatter(
        x=data.index,
        y=data["Ichimoku_Min"],
        line=dict(color="green", width=1),
        name="Ichimoku Min",
    )
)
fig.add_trace(
    go.Scatter(
        x=data.index,
        y=data["Ichimoku_Max"],
        line=dict(color="purple", width=1),
        name="Ichimoku Max",
    )
)
fig.update_xaxes(rangebreaks=[dict(values=data.index[:-1000])])
fig.update_yaxes(range=[6.4, 6.9])
fig.update_layout(xaxis_rangeslider_visible=False)
fig.show()
# ------------------------------------

### __Stratégie__

Dans la suite, on note $P_t$ le prix de clôture à la date $t$. La stratégie est la suivante :

- Si $P_{t-1} < \text{(Ichimoku Max)}_{t-1}$ et $P_t > \text{(Ichimoku Max)}_t$, alors on achète.
- Si $P_{t-1} > \text{(Ichimoku Min)}_{t-1}$ et $P_t < \text{(Ichimoku Min)}_t$, alors on vend.
- Si $P_t < \text{(Ichimoku Max)}_t$ et $P_t > \text{(Ichimoku Min)}_t$, alors on ne fait rien.

On compare notre stratégie avec un investissement passif (ici Buy and Hold).

In [3]:
# solde de départ
S = 100
FEES = 0 # Pour l'instant on ne prend pas en compte les frais de transaction
portfolio_values = []
portfolio_values_buy_and_hold = [100]
nb_transaction = 0
sell = False
buy = False
signals = []

for index, row in data[:-1].iterrows():

    row_next = data.shift(-1).loc[index]
    row_precedent = data.shift(1).loc[index]

    P_t = row["Close"] # prix de l'actif à l'instant t
    P_t_1 = row_next["Close"] # prix de l'actif à l'instant t+1
    P_t_moins_1 = row_precedent["Close"] # prix de l'actif à l'instant t-1

    #-----------------------BUY-----------------------------------
    # On passe en achat lorsqu'on pase au dessus du nuage Ichimoku
    if (
        row_precedent["Ichimoku_Max"] >= P_t_moins_1
        and row["Ichimoku_Max"] < P_t
    ):
        buy = True
        nb_transaction += 1
        S -= FEES * S # frais de transaction
    #--------------------------------------------------------------
    #-----------------------SELL-----------------------------------
    # On passe en vente lorsqu'on pase au dessus du nuage Ichimoku
    if (
        row_precedent["Ichimoku_Min"] <= P_t_moins_1
        and row["Ichimoku_Min"] > P_t
    ):
        sell = True
        nb_transaction += 1
        S -= FEES * S # frais de transaction
    #--------------------------------------------------------------
    #-----------------------CANCEL---------------------------------
    if row["Ichimoku_Max"] > P_t:
        if buy:
            S -= FEES * S
        buy = False

    if row["Ichimoku_Min"] < P_t:
        if sell:
            S -= FEES * S
        sell = False
    #--------------------------------------------------------------
    #-----------------------UPDATE---------------------------------
    if sell:
        S -= (P_t_1 - P_t) / P_t * S # S_{t+1} = S_t - (P_{t+1} - P_t) / P_t * S_t
    if buy:
        S += (P_t_1 - P_t) / P_t * S # S_{t+1} = S_t + (P_{t+1} - P_t) / P_t * S_t
    portfolio_values_buy_and_hold.append(portfolio_values_buy_and_hold[-1] + (P_t_1 - P_t) / P_t * portfolio_values_buy_and_hold[-1])
    #--------------------------------------------------------------

    print(f"Date: {index}, Buy: {buy}, Sell: {sell}, S: {S:.2f} €\r", end="")

    portfolio_values.append(S)
    signals.append(1 if buy else -1 if sell else 0)

signals.append(0)
print("\n")
print(f"Nombre de transaction effectué: {nb_transaction}")
print("Valorisation du portefeuille: {:.2f}€".format(S))

# Plot portfolio values using plotly
#------------------------------------
fig = go.Figure()
fig.add_trace(go.Scatter(x=data.index, y=portfolio_values, mode="lines", name="Ichimoku Strategy"))
fig.update_layout(title="Portfolio values", xaxis_title="Date", yaxis_title="Value")
fig.add_trace(go.Scatter(x=data.index, y=portfolio_values_buy_and_hold, mode="lines", name="Buy and Hold"))
fig.show()
#------------------------------------

Date: 2024-02-11 10:45:00, Buy: False, Sell: True, S: 519.96 €€

Nombre de transaction effectué: 1154
Valorisation du portefeuille: 519.96€


En pratique on fait les calculs de manière vectorielle pour accélérer le processus. Pour cela on utilise pandas et numpy.

In [4]:
initial_portfolio_value = 100
FEES = 0 # Pour l'instant on ne prend pas en compte les frais de transaction

data["signal"] = signals
data["portfolio_return"] = data["signal"] * (data["Close"].shift(-1) - data["Close"]) / data["Close"] 
data["portfolio_return"] -= FEES * np.abs(data["signal"].diff())
data["cum_portfolio_return"] = initial_portfolio_value * (1 + data["portfolio_return"]).cumprod()
data["buy_and_hold"] = (
    initial_portfolio_value * (1 + data["Close"].pct_change()).cumprod()
)

fig = go.Figure()
fig.add_trace(go.Scatter(x=data.index, y=data["cum_portfolio_return"], mode="lines", name="Strategy"))
fig.add_trace(go.Scatter(x=data.index, y=data["buy_and_hold"], mode="lines", name="Buy and hold"))
fig.update_layout(title="Portfolio values", xaxis_title="Date", yaxis_title="Value")
fig.show()

Maintenant, Relancez le code ci-dessus en rajoutant des fees de 0.1% à chaque transaction.

### __Analyse de la stratégie__

__Quantstats__ est une librairie qui permet de faire des analyses sur les stratégies de trading. On peut par exemple calculer le profit, le drawdown, le nombre de trades, etc. En exécutant le code ci-dessous, on obtient un résumé de la stratégie dans un fichier HTML.

In [5]:
# quantstats
import quantstats as qs

qs.extend_pandas()

data = data.dropna()

qs.reports.html(
    returns=data["cum_portfolio_return"],
    benchmark=data["buy_and_hold"],
    output="ichimoku_strategy.html",
    title="Ichimoku Strategy",
)